## Introduction

Participants will work with the **Ahmed body** benchmark — a canonical problem in automotive aerodynamics — to build a surrogate model. The course blends classical CFD data handling with modern AI-based modeling. 
For the sake of education here we will use only **Ahmed Body Surface data** for training and not volume data. 

## Course Modules

### 0. [Dataset download](#download-ahmed-body-surface-dataset)

### 1. [Preprocessing Ahmed body dataset for training with DoMINO](domino-data-preprocessing.ipynb)
- Loading and understanding VTK simulation data
- Data normalization techniques for ML
- Extracting key physical quantities
- Creating standardized datasets for training

### 2. [Training and Inferencing DoMINO Model](domino-training-test.ipynb)
- Understanding DoMINO architecture and physics-informed learning
- Training process
- Load Model Checkpoint & Run Inference
- Visualizing the predicted results

### Hardware Requirements
- NVIDIA GPU with CUDA support
- 4GB+ RAM
- 100GB+ disk space

### Software Requirements
- Docker with NVIDIA Container Toolkit
- NVIDIA Drivers (version 545 or later)
- SLURM workload manager

## Quick Start Guide

### Course Environment
This course is set up to use the the PhysicsNeMo docker environment from NVIDIA NGC, and all other additional dependencies are already installed. If you wish to set up the environment outside of this space, the following steps can be used, but note, they are not necessary for this HuggingFace Space.

### Required Setup Steps
The only required step is to pull the dataset from NVIDIA NGC.

#### Download Ahmed Body surface dataset

The complete Ahmed body surface dataset is hosted on NGC and accessible from the following link:

https://catalog.ngc.nvidia.com/orgs/nvidia/teams/physicsnemo/resources/physicsnemo_ahmed_body_dataset

The data can be downloaded using the NVIDIA NGC cli. Please note that the dataset contains VTP files, but training DoMINO and X-MeshGraphNet also requires STL files. Therefore, in the `domino-data-preprocessing.ipynb` notebook, STL files are extracted from the available VTP data.

The data should be available in this space already at "/data/physicsnemo_ahmed_body_dataset_vv1". If it is not, we can download it again:

In [ ]:
!if [ ! -d "/data/physicsnemo_ahmed_body_dataset_vv1" ]; then \
    echo "Dataset not found. Downloading..."; \
    ~/app/ngc-cli/ngc registry resource download-version "nvidia/physicsnemo/physicsnemo_ahmed_body_dataset:v1" --dest /data; \
else \
    echo "Dataset already exists at /data/physicsnemo_ahmed_body_dataset_vv1"; \
fi

### Optional Steps for Standalone Environment Setup

The next set of steps are only necessary if you would like to rebuild the environment outside of HuggingFace Spaces.

Once the dataset is downloaded, you man procede to [domino-data-preprocessing.ipynb](domino-data-preprocessing.ipynb)!

#### Setting your environment to pull the PhysicsNeMo container from NGC:

Please refer to the following link for instructions on setting up your environment to pull the PhysicsNeMo container from NGC:
https://docs.nvidia.com/launchpad/ai/base-command-coe/latest/bc-coe-docker-basics-step-02.html


#### Running PhysicsNeMo container using docker command

Pull the PhysicsNeMo container with the following command:
```bash
docker pull nvcr.io/nvidia/physicsnemo/physicsnemo:25.06
 ```

To launch the PhysicsNeMo container using docker, use the following command:

```bash
docker run --gpus 1  --shm-size=2g -p 7008:7008 --ulimit memlock=-1 --ulimit stack=67108864 --runtime nvidia -v <path_on_host>:/workspace -it --rm $(docker images | grep 25.03| awk '{print $3}')
 
```

Make sure to replace <path_on_host> with the absolute path to the directory on the host system that contains your Jupyter notebooks and Ahmed Body surface data. This path will be mounted as `/workspace` inside the container, providing access to your data and scripts during the session

#### Start Jupyter Lab

From the terminal inside the container run the following command to start Jupyter Lab in the background:

```bash
nohup python3 -m jupyter lab --ip=0.0.0.0 --port=7008 --allow-root  --no-browser --NotebookApp.token='' --notebook-dir='/workspace/' --NotebookApp.allow_origin='*' > /dev/null 2>&1 &
```

Then from your labtop start a SSH tunnel using the host which your job is running and the port which you assigned above `--port=1234`: 

```bash
ssh -L 3030:eos0311:7008 eos
```
Access Jupyter Lab using `http://localhost:1234` in your browser. 

#### Dependencies

Please install the following in the container.
```bash
pip install numpy pyvista vtk matplotlib tqdm numpy-stl torchinfo
apt install  xvfb
```

## Troubleshooting

### Common Issues

1. **Memory Issues**
   - Monitor GPU memory: `nvidia-smi`
   - Check system memory: `free -h`

2. **GPU Support**

   - Run the following command to verify your container runtime supports NVIDIA GPUs:

```bash
docker run --rm --runtime=nvidia --gpus all ubuntu nvidia-smi
```

Expected output should show your GPU information, for example:
```
+-----------------------------------------------------------------------------------------+
| NVIDIA-SMI 560.35.03              Driver Version: 560.35.03      CUDA Version: 12.6     |
|-----------------------------------------+------------------------+----------------------+
| GPU  Name                 Persistence-M | Bus-Id          Disp.A | Volatile Uncorr. ECC |
| Fan  Temp   Perf          Pwr:Usage/Cap |           Memory-Usage | GPU-Util  Compute M. |
|                                         |                        |               MIG M. |
|=========================================+========================+======================|
|   0  NVIDIA A100-PCIE-40GB          Off |   00000000:41:00.0 Off |                    0 |
| N/A   37C    P0             35W /  250W |   40423MiB /  40960MiB |      0%      Default |
|                                         |                        |             Disabled |
+-----------------------------------------+------------------------+----------------------+
```

## Additional Resources

- [NVIDIA Physics NeMo Documentation](https://docs.nvidia.com/deeplearning/nemo-physics/user-guide)
- [PyVista Documentation](https://docs.pyvista.org/) for 3D visualization
- [Ahmed Body Benchmark](https://www.cfd-online.com/Wiki/Ahmed_body) for background
- [Physics-Informed Neural Networks](https://www.sciencedirect.com/science/article/abs/pii/S0021999118307125) paper
- [Graph Neural Networks](https://arxiv.org/abs/2106.10943) for scientific computing
- [Neural Operators](https://arxiv.org/abs/2108.08481) for PDEs
- [DGL Documentation](https://www.dgl.ai/) for graph neural networks
- [Triton Inference Server](https://github.com/triton-inference-server/server) for deployment
